Required libraries 

In [51]:
import pandas as pd 
import numpy as np 
from sklearn.model_selection import train_test_split
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix
from sklearn.metrics import accuracy_score
from sklearn import tree


Steps:

In [ ]:
df = pd.read_csv('spambase_data.csv', header=None) #here I used the spambase dataset  

SyntaxError: invalid syntax (709673341.py, line 1)

In [53]:
X = df [df.columns [:-1]]
Y = df [len (df.columns)-1]

In [54]:
X_train, X_test, Y_train, Y_test =train_test_split(X, Y, test_size=0.20, random_state =30)

In [55]:
dtree = DecisionTreeClassifier()
dtree.fit (X_train, Y_train)


DecisionTreeClassifier()

In [56]:
predictions = dtree.predict(X_test)

In [57]:
print (classification_report (Y_test, predictions))
print ("Confusion Matrix")
print (confusion_matrix (Y_test, predictions))
print ("\n Accuracy")
print (accuracy_score (Y_test, predictions))

              precision    recall  f1-score   support

           0       0.91      0.93      0.92       578
           1       0.88      0.85      0.86       343

    accuracy                           0.90       921
   macro avg       0.89      0.89      0.89       921
weighted avg       0.90      0.90      0.90       921

Confusion Matrix
[[537  41]
 [ 53 290]]

 Accuracy
0.8979370249728555


Visualization of tree:

In [58]:
import matplotlib.pyplot as plt
fig, axes = plt.subplots(nrows = 1,ncols = 1,figsize = (16,16), dpi=1024)
tree.plot_tree(dtree)
fig.savefig('decision_tree.png')

QUE 1. Create a decision stump and find the majority class, error.

In [59]:
from sklearn.tree import DecisionTreeClassifier

stump = DecisionTreeClassifier(max_depth=1, random_state=30)
stump.fit(X_train, Y_train)

stump_predictions = stump.predict(X_test)
print("Decision Stump Classification Report:")
print(classification_report(Y_test, stump_predictions))
print("Confusion Matrix:")
print(confusion_matrix(Y_test, stump_predictions))
print("Accuracy:", accuracy_score(Y_test, stump_predictions))

majority_class = Y_train.value_counts().idxmax()
majority_class_error = 1 - (Y_test == majority_class).mean()
print("Majority Class:", majority_class)
print("Majority Class Error:", majority_class_error)


Decision Stump Classification Report:
              precision    recall  f1-score   support

           0       0.82      0.83      0.82       578
           1       0.71      0.70      0.70       343

    accuracy                           0.78       921
   macro avg       0.76      0.76      0.76       921
weighted avg       0.78      0.78      0.78       921

Confusion Matrix:
[[478 100]
 [104 239]]
Accuracy: 0.7785016286644951
Majority Class: 0
Majority Class Error: 0.37242128121606954


QUE 2. Create a DT classifier using entropy to measure the quality of split. (random state parameter of the DT classifier can take integer values from. We will be using random state value as 30.)


In [60]:
dtree_entropy = DecisionTreeClassifier(criterion='entropy', random_state=30)
dtree_entropy.fit(X_train, Y_train)

entropy_predictions = dtree_entropy.predict(X_test)
print("Entropy Decision Tree Classification Report:")
print(classification_report(Y_test, entropy_predictions))
print("Accuracy:", accuracy_score(Y_test, entropy_predictions))


Entropy Decision Tree Classification Report:
              precision    recall  f1-score   support

           0       0.93      0.94      0.93       578
           1       0.90      0.87      0.88       343

    accuracy                           0.91       921
   macro avg       0.91      0.91      0.91       921
weighted avg       0.91      0.91      0.91       921

Accuracy: 0.9142236699239956


QUE 3. Compare the two trees on the basis of their accuracy. Which tree gives better accuracy (using gini index or entropy).


In [61]:
stump_acc = accuracy_score(Y_test, stump_predictions)
entropy_acc = accuracy_score(Y_test, entropy_predictions)

print("Stump Accuracy:", stump_acc)
print("Entropy Tree Accuracy:", entropy_acc)

if entropy_acc > stump_acc:
    print("Entropy-based tree performs better.")
else:
    print("Decision stump performs better or equal.")


Stump Accuracy: 0.7785016286644951
Entropy Tree Accuracy: 0.9142236699239956
Entropy-based tree performs better.


QUE 4. Fully grown decision tree usually over-fits the data. To overcome the problem of overfitting, pruning techniques are used. One of which is restricting the height of the tree. Find the value of the height for which the decision tree model is giving the highest accuracy. (Use entropy measure)


In [62]:
best_depth = 0
best_accuracy = 0
depth_accuracies = []

for depth in range(1, 21):
    dt = DecisionTreeClassifier(criterion='entropy', max_depth=depth, random_state=30)
    dt.fit(X_train, Y_train)
    preds = dt.predict(X_test)
    acc = accuracy_score(Y_test, preds)
    depth_accuracies.append((depth, acc))
    
    if acc > best_accuracy:
        best_accuracy = acc
        best_depth = depth

print("Best Depth:", best_depth)
print("Best Accuracy at that depth:", best_accuracy)


Best Depth: 16
Best Accuracy at that depth: 0.9131378935939196


QUE Find the feature importance from the trained model and rebuild the model using top 10 important features only. The required library and function is given in the hint.
Hint: import heapq
feature_imp = dtree_entropy.feature_importances_
print (feature_imp)
Is there any information loss in the tree created above?

In [ ]:
import heapq

feature_imp = dtree_entropy.feature_importances_
print("Feature Importances:", feature_imp)

top_10_indices = heapq.nlargest(10, range(len(feature_imp)), key=feature_imp.__getitem__)
print("Top 10 Important Feature Indices:", top_10_indices)

X_train_top10 = X_train.iloc[:, top_10_indices]
X_test_top10 = X_test.iloc[:, top_10_indices] 

dtree_top10 = DecisionTreeClassifier(criterion='entropy', random_state=30)
dtree_top10.fit(X_train_top10, Y_train)

pred_top10 = dtree_top10.predict(X_test_top10)
print("Top 10 Features Model Accuracy:", accuracy_score(Y_test, pred_top10))

if accuracy_score(Y_test, pred_top10) < entropy_acc:
    print("Some information is lost using only top 10 features.")
else:
    print("No significant information loss with top 10 features.")

Feature Importances: [0.00116017 0.0071889  0.00080643 0.00196433 0.01858134 0.00084887
 0.12164025 0.01089364 0.         0.00698211 0.00613611 0.00838193
 0.00152774 0.         0.0014958  0.03679318 0.00829446 0.00207265
 0.01896218 0.         0.02172866 0.         0.00571484 0.00097175
 0.05396495 0.00288217 0.02566494 0.00077169 0.         0.00277195
 0.         0.         0.00372146 0.         0.         0.
 0.00585022 0.00154339 0.         0.         0.00116017 0.00515844
 0.00370181 0.00285512 0.01240328 0.02566968 0.         0.
 0.00381864 0.01237202 0.         0.28899474 0.12550709 0.
 0.07438123 0.03510952 0.02955216]
Top 10 Important Feature Indices: [51, 52, 6, 54, 24, 15, 55, 56, 45, 26]
Top 10 Features Model Accuracy: 0.9066232356134636
Some information is lost using only top 10 features.
